In [1]:
import tensorflow as tf
import numpy as np
from tensorflow import keras
from keras.layers import Input, Lambda, Dense, Flatten, Rescaling
from keras.models import Model

In [2]:
#loading data
train_ds = np.load("../input/cats-and-dog-classification/images_train.npy")
test_ds = np.load("../input/cats-and-dog-classification/images_test.npy")
cv_ds = np.load("../input/cats-and-dog-classification/images_valid.npy")

labels_train = np.load("../input/cats-and-dog-classification/labels_train.npy")
labels_test = np.load("../input/cats-and-dog-classification/labels_test.npy")
labels_cv = np.load("../input/cats-and-dog-classification/labels_valid.npy")

In [3]:
len(labels_train)

600

In [4]:
cv_ds.shape

(300, 160, 160, 3)

In [5]:
base_model = keras.applications.Xception(
    weights = "../input/xception/xception_weights_tf_dim_ordering_tf_kernels_notop.h5", 
    input_shape = (160,160,3), 
    include_top = False,)

base_model.trainable = False

2022-09-06 05:09:56.578134: I tensorflow/core/common_runtime/process_util.cc:146] Creating new thread pool with default inter op setting: 2. Tune using inter_op_parallelism_threads for best performance.


In [6]:
#Xception model
#creating/adding new layers on top of base model
inputs = keras.Input(shape = (160,160,3))
#normalizing pixel values
x = Rescaling(scale = 1/127.5, offset = -1)(inputs)
x = base_model(x, training = False)
x = keras.layers.GlobalAveragePooling2D()(x)
outputs = keras.layers.Dense(1,activation = 'sigmoid')(x)
model = keras.Model(inputs, outputs)

model.compile(
    loss = keras.losses.BinaryCrossentropy(),
    optimizer = keras.optimizers.Adam(0.01),
    metrics = ["accuracy"]
)

model.summary()

Model: "model"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         [(None, 160, 160, 3)]     0         
_________________________________________________________________
rescaling (Rescaling)        (None, 160, 160, 3)       0         
_________________________________________________________________
xception (Functional)        (None, 5, 5, 2048)        20861480  
_________________________________________________________________
global_average_pooling2d (Gl (None, 2048)              0         
_________________________________________________________________
dense (Dense)                (None, 1)                 2049      
Total params: 20,863,529
Trainable params: 2,049
Non-trainable params: 20,861,480
_________________________________________________________________


In [7]:
model.fit(train_ds, labels_train, epochs = 10, batch_size = 64)

2022-09-06 05:10:00.075940: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:185] None of the MLIR Optimization Passes are enabled (registered 2)


Epoch 1/10
10/10 [==============================] - 29s 2s/step - loss: 0.2673 - accuracy: 0.8667
Epoch 2/10
10/10 [==============================] - 24s 2s/step - loss: 0.0918 - accuracy: 0.9533
Epoch 3/10
10/10 [==============================] - 25s 2s/step - loss: 0.0525 - accuracy: 0.9750
Epoch 4/10
10/10 [==============================] - 25s 2s/step - loss: 0.0231 - accuracy: 0.9917
Epoch 5/10
10/10 [==============================] - 25s 2s/step - loss: 0.0124 - accuracy: 1.0000
Epoch 6/10
10/10 [==============================] - 26s 3s/step - loss: 0.0096 - accuracy: 1.0000
Epoch 7/10
10/10 [==============================] - 24s 2s/step - loss: 0.0081 - accuracy: 1.0000
Epoch 8/10
10/10 [==============================] - 25s 2s/step - loss: 0.0059 - accuracy: 1.0000
Epoch 9/10
10/10 [==============================] - 25s 2s/step - loss: 0.0049 - accuracy: 1.0000
Epoch 10/10
10/10 [==============================] - 25s 2s/step - loss: 0.0044 - accuracy: 1.0000


In [8]:
#infereing before fine tuning
import time
start = time.time()
y_pred_cv = model.predict(cv_ds)
end = time.time()

In [9]:
print("Time in ms: ",1000*(end-start))

Time in ms:  13663.084030151367


In [10]:
y_pred = y_pred_cv
for i in range(len(y_pred_cv)):
    if y_pred_cv[i] > 0.5:
        y_pred[i] = 1
    else:
        y_pred[i] = 0

In [11]:
for i in range(len(y_pred_cv)//10):
    print(labels_cv[i], y_pred[i])

0 [0.]
0 [0.]
1 [1.]
1 [0.]
0 [0.]
0 [0.]
0 [0.]
0 [0.]
0 [0.]
1 [1.]
1 [0.]
0 [0.]
1 [1.]
1 [1.]
1 [1.]
1 [1.]
0 [0.]
1 [1.]
0 [0.]
0 [0.]
1 [1.]
1 [1.]
0 [0.]
0 [0.]
0 [0.]
1 [1.]
1 [1.]
1 [1.]
0 [0.]
1 [1.]


In [12]:
model.evaluate(cv_ds,labels_cv)

10/10 [==============================] - 14s 1s/step - loss: 0.1030 - accuracy: 0.9633


[0.10299235582351685, 0.9633333086967468]

In [13]:
#function for opening and resizing img
def img_pros(path):
    img = open(path,'rb')
    img = img.read()
    img = tf.image.decode_jpeg(img)
    img =tf.image.resize(img, [160,160])
    img = tf.expand_dims(img, axis = 0)
    return img

In [15]:
#testing on cats and dog imgs before fine tuning
#predicting images of cats from internet
from PIL import Image
import tensorflow_datasets as tfds

img_n = img_pros("../input/cat-pic/raoul-droog-yMSecCHsIBc-unsplash.jpg")
start = time.time()
pred_n = model.predict(img_n)
end = time.time()
print("Time in ms: ",1000*(end-start))
print(pred_n)
label = [1]
label = np.array(label)
model.evaluate(img_n,label)

img_n = img_pros("../input/catpic/karina-vorozheeva-rW-I87aPY5Y-unsplash.jpg")
start = time.time()
pred_n = model.predict(img_n)
end = time.time()
print("Time in ms: ",1000*(end-start))
print(pred_n)
label = [1]
label = np.array(label)
model.evaluate(img_n,label)

img_n = img_pros("../input/catpicn/timothy-meinberg-AL2-t0GrSko-unsplash.jpg")
start = time.time()
pred_n = model.predict(img_n)
end = time.time()
print("Time in ms: ",1000*(end-start))
print(pred_n)
label = [1]
label = np.array(label)
model.evaluate(img_n,label)

Time in ms:  288.85865211486816
[[0.58652806]]
1/1 [==============================] - 1s 1s/step - loss: 0.5335 - accuracy: 1.0000
Time in ms:  146.4993953704834
[[0.9971067]]
1/1 [==============================] - 0s 129ms/step - loss: 0.0029 - accuracy: 1.0000
Time in ms:  145.5082893371582
[[0.00500447]]
1/1 [==============================] - 0s 125ms/step - loss: 5.2974 - accuracy: 0.0000e+00


[5.297418594360352, 0.0]

In [16]:
#testing on cats and dog imgs before fine tuning
#predicting images of dogs from 

img_n = img_pros("../input/dog-pic-n/richard-brutyo-Sg3XwuEpybU-unsplash.jpg")
start = time.time()
pred_n = model.predict(img_n)
end = time.time()
print("Time in ms: ",1000*(end-start))
print(pred_n)
label = [0]
label = np.array(label)
model.evaluate(img_n,label)

img_n = img_pros("../input/dogpic/alvan-nee-brFsZ7qszSY-unsplash.jpg")
start = time.time()
pred_n = model.predict(img_n)
end = time.time()
print("Time in ms: ",1000*(end-start))
print(pred_n)
label = [0]
label = np.array(label)
model.evaluate(img_n,label)

Time in ms:  150.8650779724121
[[0.00194362]]
1/1 [==============================] - 0s 126ms/step - loss: 0.0019 - accuracy: 1.0000
Time in ms:  143.8894271850586
[[0.00160024]]
1/1 [==============================] - 0s 126ms/step - loss: 0.0016 - accuracy: 1.0000


[0.0016015038127079606, 1.0]

In [17]:
#fine tuning
#fine tuning by using a very small learning rate
base_model.trainable = True

model.compile(
    loss = keras.losses.BinaryCrossentropy(),
    optimizer = keras.optimizers.Adam(1e-5),
    metrics = ["accuracy"]
)

model.fit(train_ds, labels_train, epochs = 10, batch_size = 64)

Epoch 1/10
10/10 [==============================] - 100s 9s/step - loss: 0.0039 - accuracy: 1.0000
Epoch 2/10
10/10 [==============================] - 91s 9s/step - loss: 5.6470e-04 - accuracy: 1.0000
Epoch 3/10
10/10 [==============================] - 92s 9s/step - loss: 2.2898e-04 - accuracy: 1.0000
Epoch 4/10
10/10 [==============================] - 91s 9s/step - loss: 1.2756e-04 - accuracy: 1.0000
Epoch 5/10
10/10 [==============================] - 91s 9s/step - loss: 8.9888e-05 - accuracy: 1.0000
Epoch 6/10
10/10 [==============================] - 92s 9s/step - loss: 6.8200e-05 - accuracy: 1.0000
Epoch 7/10
10/10 [==============================] - 92s 9s/step - loss: 5.5783e-05 - accuracy: 1.0000
Epoch 8/10
10/10 [==============================] - 91s 9s/step - loss: 4.6846e-05 - accuracy: 1.0000
Epoch 9/10
10/10 [==============================] - 91s 9s/step - loss: 4.0850e-05 - accuracy: 1.0000
Epoch 10/10
10/10 [==============================] - 91s 9s/step - loss: 3.5488e-05 -

In [31]:
import time
start = time.time()
y_pred_cv = model.predict(cv_ds)
end = time.time()
print("Time in ms: ",1000*(end-start))

Time in ms:  12530.858755111694


In [32]:
model.evaluate(cv_ds,labels_cv)

10/10 [==============================] - 13s 1s/step - loss: 0.1364 - accuracy: 0.9633


[0.1364215910434723, 0.9633333086967468]

In [44]:
#predicting a image of cat from internet
from PIL import Image
import tensorflow_datasets as tfds

size = (160,160)
img = open("../input/cat-pic/raoul-droog-yMSecCHsIBc-unsplash.jpg",'rb')
img = img.read()
img = tf.image.decode_jpeg(img)
img =tf.image.resize(img, [160,160])
img = tf.expand_dims(img, axis = 0)
start = time.time()
pred = model.predict(img)
end = time.time()
print(1000*(end-start))
print(pred)
label = [1]
label = np.array(label)
model.evaluate(img,label)



img_n = img_pros("../input/catpic/karina-vorozheeva-rW-I87aPY5Y-unsplash.jpg")
start = time.time()
pred_n = model.predict(img_n)
end = time.time()
print("Time in ms: ",1000*(end-start))
print(pred_n)
label = [1]
label = np.array(label)
model.evaluate(img_n,label)



img_n = img_pros("../input/catpicn/timothy-meinberg-AL2-t0GrSko-unsplash.jpg")
start = time.time()
pred_n = model.predict(img_n)
end = time.time()
print("Time in ms: ",1000*(end-start))
print(pred_n)
label = [1]
label = np.array(label)
model.evaluate(img_n,label)

179.65960502624512
[[0.5791096]]
1/1 [==============================] - 0s 134ms/step - loss: 0.5463 - accuracy: 1.0000
Time in ms:  165.0869846343994
[[0.999676]]
1/1 [==============================] - 0s 128ms/step - loss: 3.2397e-04 - accuracy: 1.0000
Time in ms:  153.2268524169922
[[0.00013429]]
1/1 [==============================] - 0s 129ms/step - loss: 8.9155 - accuracy: 0.0000e+00


[8.915472030639648, 0.0]

In [46]:
img_n = img_pros("../input/dog-pic-n/richard-brutyo-Sg3XwuEpybU-unsplash.jpg")
start = time.time()
pred_n = model.predict(img_n)
end = time.time()
print("Time in ms: ",1000*(end-start))
print(pred_n)
label = [0]
label = np.array(label)
model.evaluate(img_n,label)

img_n = img_pros("../input/dogpic/alvan-nee-brFsZ7qszSY-unsplash.jpg")
start = time.time()
pred_n = model.predict(img_n)
end = time.time()
print("Time in ms: ",1000*(end-start))
print(pred_n)
label = [0]
label = np.array(label)
model.evaluate(img_n,label)

Time in ms:  179.96501922607422
[[5.871874e-06]]
1/1 [==============================] - 0s 132ms/step - loss: 5.8719e-06 - accuracy: 1.0000
Time in ms:  153.44476699829102
[[0.00022373]]
1/1 [==============================] - 0s 130ms/step - loss: 2.2373e-04 - accuracy: 1.0000


[0.00022372744570020586, 1.0]

In [43]:
#conisder data augmentation